In [1]:
class treeNode: 
    def __init__(self, nameValue, numOccur, parentNode):
        self.name = nameValue
        self.count = numOccur
        self.nodeLink = None
        self.parent = parentNode
        self.children= {}
    
    def inc(self, numOccur):
        self.count += numOccur
    
    def disp(self, ind=1):
        print (' '*ind, self.name, ' ', self.count)
        for child in self.children.values():
            child.disp(ind+1)
    
 

In [2]:
def createTree(dataSet, minSup):
    headerTable = {}
    for trans in dataSet:
        for item in trans:
            headerTable[item] =headerTable.get(item, 0) + dataSet[trans]
    for k in list(headerTable):
        if headerTable[k] < minSup:
            del (headerTable[k])
    freqItemSet = set(list(headerTable))
    if len(freqItemSet) == 0:
        return None, None
    for k in headerTable:
        headerTable[k] = [headerTable[k], None]
    retTree = treeNode('Null Set', 1, None)
    for tranSet, count in dataSet.items():
        localD = {}
        for item in tranSet:
            if item in freqItemSet:
                localD[item] = headerTable[item][0]
        if len(localD) > 0:
            orderedItems = [v[0] for v in sorted(localD.items(), key=lambda p:p[1], reverse=True)]
            updateTree(orderedItems, retTree, headerTable, count)
    return retTree, headerTable
        


In [3]:
def updateTree(items, inTree, headerTable, count):
    if items[0] in inTree.children:
        inTree.children[items[0]].inc(count)
    else:
        inTree.children[items[0]] = treeNode(items[0], count, inTree)
        if headerTable[items[0]][1] == None:
            headerTable[items[0]][1] = inTree.children[items[0]]
        else: 
            updateHeader(headerTable[items[0]][1],
                        inTree.children[items[0]])
            
    if len(items) > 1:
        updateTree(items[1::], inTree.children[items[0]], headerTable, count)

In [4]:
def ascendTree(leafNode, prefixPath):
    if leafNode.parent != None:
        prefixPath.append(leafNode.name)
        ascendTree(leafNode.parent, prefixPath)

In [5]:
def findPrefixPath(basePat, treeNode):
    condPats = {}
    while treeNode != None:
        prefixPath = []
        ascendTree(treeNode, prefixPath)
        if len(prefixPath) > 1:
            condPats[frozenset(prefixPath[1:])] = treeNode.count
        treeNode = treeNode.nodeLink
    return condPats
        

In [6]:
def updateHeader(nodeToTest, targetNode):
    while (nodeToTest.nodeLink != None):
        nodeToTest = nodeToTest.nodeLink
    nodeToTest.nodeLink = targetNode

In [7]:
def StrArray(itemset):
    import re
    
    index = []
    coba = []
    idx = []
    items = []
    sub = []
    
    #mengubah baris menjadi array dalam array
    for arr in itemset:
        for row in arr:
            coba = row.split(',')
            index.append(coba)
            
    #menghapus Whitespaces dari String menggunakan Regex   
    for arr in index:
        for row in range(len(arr)):
            idx = re.sub(r"^\s+|\s+$", "", arr[row])
            arr[row] = idx
        items.append(arr)
        
    #menghapus item yang duplikat dalam satu satu itemset
    for arr in items:
        for row in arr:
            if arr.count(row) > 1 :
                arr.remove(row)    
        sub.append(arr)
        
    return sub

In [8]:
def FpGrowth(dataset, min_support):
    import pandas as pd
    from mlxtend.preprocessing import TransactionEncoder
    from mlxtend.frequent_patterns import fpgrowth
    
    te = TransactionEncoder()
    te_ary = te.fit(dataset).transform(dataset)
    df = pd.DataFrame(te_ary, columns=te.columns_)
    #fpgrowth(df, min_support)
    data = fpgrowth(df, min_support, use_colnames=True)
    
    return data
    
    

In [9]:
def loadSimpDat():
    import pandas as pd
    import re
    #mengambil data
    data = pd.read_csv("F:/Catatan Materi/Semester 7/DAMI_PD/Projek/Dataset/FIX/BigML.csv")
    #menghapus baris yang memiliki nilai null atau NAN
    data1 = data.dropna()
    #mengambil rows atau baris sebanyak 11000
    products = data1[:11000]
    #mengubah karakter "|" menjadi komma (,) dan menampungnya di atribut baru yaitu 'changes_line'
    products['Changes_line'] = products['products'].apply(lambda x: 
                                                    [re.sub(r"[\|\&]", ", ", word) for word in x.split(',')])
    
    #mengambil kolom changes_line
    data2=products["Changes_line"].tolist()
    data3= StrArray(data2)
    
    
    #mengubah row atau baris menjadi array dalam array
   
    
    """simpDat = [['jojo milk asli susu kambing', 'teh sosor selerah ayam', 'fresker alay baba hoho'],
                ["teh sosor  selerah ayam", "masker kulit kerbau", "betadin"],
                ["jojo milk asli susu kambing", "masker kulit kerbau", "fresker alay baba hoho"],
                ["teh sosor selerah ayam", "sari roti"],
                ["bear", "jojo milk asli susu kambing", "teh sosor selerah ayam"],
                ["bear", "jojo milk asli susu kambing", "teh sosor selerah ayam", "fresker alay baba hoho"]]"""
    
    return data3

In [10]:
def createInitSet(dataSet):
    retDict = {}
    for trans in dataSet:
        retDict[frozenset(trans)] = 1
    return retDict

In [11]:
def mineTree(inTree, headerTable, minSup, preFix, freqItemList):
    bigL = [v[0] for v in sorted(headerTable.items(), key=lambda p: p[1])]
    
    for basePat in bigL:
        newFreqSet = preFix.copy()
        newFreqSet.add(basePat)
        freqItemList.append(newFreqSet)
        condPattBases = findPrefixPath(basePat, headerTable[basePat][1])
        myCondTree, myHead = createTree(condPattBases, minSup)
        
        if myHead != None:
            mineTree(myCondTree, myHead, minSup, newFreqset, freqItemList)

In [12]:
simpDat = loadSimpDat()

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # This is added back by InteractiveShellApp.init_path()


In [13]:
simpDat

[['Bulgarian Yogurt',
  'Organic 4% Milk Fat Whole Milk Cottage Cheese',
  'Organic Celery Hearts',
  'Cucumber Kirby',
  'Lightly Smoked Sardines in Olive Oil',
  'Bag of Organic Bananas',
  'Organic Hass Avocado',
  'Organic Whole String Cheese'],
 ['Organic Egg Whites',
  'Michigan Organic Kale',
  'Garlic Powder',
  'Coconut Butter',
  'Natural Sweetener',
  'Carrots',
  'Original Unflavored Gelatine Mix',
  'All Natural No Stir Creamy Almond Butter',
  'Classic Blend Cole Slaw'],
 ['Total 2% with Strawberry Lowfat Greek Strained Yogurt',
  'Unsweetened Almondmilk',
  'Lemons',
  'Organic Baby Spinach',
  'Unsweetened Chocolate Almond Breeze Almond Milk',
  'Organic Ginger Root',
  'Air Chilled Organic Boneless Skinless Chicken Breasts',
  'Organic Ezekiel 49 Bread Cinnamon Raisin'],
 ['Plain Pre-Sliced Bagels',
  'Honey/Lemon Cough Drops',
  'Chewy 25% Low Sugar Chocolate Chip Granola',
  'Oats',
  'Chocolate Chewy Bars',
  "Kellogg's Nutri-Grain Apple Cinnamon Cereal",
  'Nutri-G

In [14]:
initSet =  createInitSet(simpDat)

In [15]:
initSet

{frozenset({'Bag of Organic Bananas',
            'Bulgarian Yogurt',
            'Cucumber Kirby',
            'Lightly Smoked Sardines in Olive Oil',
            'Organic 4% Milk Fat Whole Milk Cottage Cheese',
            'Organic Celery Hearts',
            'Organic Hass Avocado',
            'Organic Whole String Cheese'}): 1,
 frozenset({'All Natural No Stir Creamy Almond Butter',
            'Carrots',
            'Classic Blend Cole Slaw',
            'Coconut Butter',
            'Garlic Powder',
            'Michigan Organic Kale',
            'Natural Sweetener',
            'Organic Egg Whites',
            'Original Unflavored Gelatine Mix'}): 1,
 frozenset({'Air Chilled Organic Boneless Skinless Chicken Breasts',
            'Lemons',
            'Organic Baby Spinach',
            'Organic Ezekiel 49 Bread Cinnamon Raisin',
            'Organic Ginger Root',
            'Total 2% with Strawberry Lowfat Greek Strained Yogurt',
            'Unsweetened Almondmilk',
       

In [16]:
myFPtree, myHeaderTab = createTree(initSet, 0.01)

In [17]:
myFPtree.disp()

  Null Set   1
   Bag of Organic Bananas   1310
    Organic Hass Avocado   136
     Cucumber Kirby   1
      Organic Whole String Cheese   1
       Organic Celery Hearts   1
        Organic 4% Milk Fat Whole Milk Cottage Cheese   1
         Lightly Smoked Sardines in Olive Oil   1
          Bulgarian Yogurt   1
     Organic Raspberries   24
      Organic Garlic   2
       Organic Extra Large Grade AA Brown Eggs   1
        Red Grapefruit   1
         Calorie Free   1
          Barista Blend Pure Almond Milk   1
           Tuscan Kale   1
            Quinoa Salad   1
             Truffle Popcorn   1
              Vegetarian Chili Seasoning   1
               Organic European Style Lightly Salted Butter   1
                Vanilla Frozen Non-Dairy Dessert Bites   1
                 Meyer Lemon Miracle Tart   1
                  El Ciprés Whole Bean Coffee   1
       Organic Grape Tomatoes   1
        Carrots   1
         Organic Small Bunch Celery   1
          Organic Granny Smith Apple

              High Pulp Orange Juice   1
     Organic Fuji Apple   5
      Apple Honeycrisp Organic   1
       Thin Stackers Brown Rice Lightly Salted   1
      Red Peppers   1
       Organic Romaine Lettuce   1
        Yellow Bell Pepper   1
         Total 0% Cherry Nonfat Yogurt   1
          Bag Of Organic Lemons   1
           Almond Snack Crackers   1
      Carrots   1
       Organic Whole String Cheese   1
        Organic Tomato Cluster   1
         Organic Granny Smith Apple   1
          Bartlett Pears   1
           Organic Romaine Lettuce   1
            Chicken   1
             Whole Milk   1
              Total 0% Greek Yogurt   1
               Ground Turkey Breast   1
                Organic Bread with 21 Whole Grains   1
                 Maple Breakfast Sausage   1
                  English Seedless Cucumber   1
                   Naturals Chicken Nuggets   1
                    Organic Chicken Strips   1
                     Yo Baby Organic Whole Milk Banana Mango Yogur

          Shredded Parmesan   1
           Organic Shredded Mozzarella   1
            Organic Spring Mix Salad   1
             Nut Food Bar   1
              Organic Whole Grain Wheat English Muffins   1
               Uncured Slow Cooked Ham   1
                Nut Bar   1
                 XL Emerald White Seedless Grapes   1
                  Sliced Black Olives   1
                   Butternut Squash   1
                    Sweet Potatoes   1
                     Organic Mixed Vegetables   1
                      Naturals Savory Turkey Breakfast Sausage   1
                       Multigrain Oat Bread   1
                        Cherry Pie Fruit   1
                         Just Green Unsweetened Tea   1
                          Real French Vinaigrette Dressing   1
                           Organic Australian Style Vanilla Lowfat Yogurt   1
                            Sesame Street Organic Mini Blueberry Pancakes   1
                             Lemon Fruit   1
                  

            Provolone   1
             Honeydew Melon   1
              Organic Cinnamon Apple Sauce   1
               Orignial Recipe Chocolate Pudding   1
                Newman O's Creme Filled Chocolate Cookies   1
                 Baking Mix   1
                  Family Recipe Italian Dressing   1
                   Sliced Pepperoncini   1
      Organic Tomato Cluster   1
       Organic Red Onion   1
        Green Bell Pepper   1
         Extra Virgin Olive Oil   1
          Organic Roasted Turkey Breast   1
           Organic Sour Cream   1
            Organic Hothouse Cucumbers   1
             Uncured Hickory Smoked Sunday Bacon   1
              Lightly Salted Baked Snap Pea Crisps   1
               White Corn   1
                Organic Extra Large Grade AA Brown Eggs   1
                 Total 0% with Honey Nonfat Greek Strained Yogurt   1
                  Organic Sunday Bacon   1
                   Organic Cream Cheese Bar   1
                    Organic Milk Reduced Fat

           Raspberry Yoghurt   1
            Lemon Yogurt   1
             Sea Salt Caramel Gelato   1
              Good Seed Organic Thin Sliced Bread   1
               Kitchen Cheese Enchilada   1
                Peach Yoghurt   1
                 Pizza Poppers Uncured Pepperoni   1
                  Organic Mango Slices   1
                   Rice Mac   1
                    Pico De Gallo Chunky Salsa   1
                     Lowfat Raspberry Kefir Probiotic Cultured Milk Smoothie   1
                      Gummy Worms Made with Organic Fruit Juice   1
                       Cheddar Multi-Grain Flatbread Breakfast Sandwich   1
                        Uncured Ham-Egg   1
     Organic Hothouse Cucumbers   1
      Cherubs Heavenly Salad Tomatoes   1
       Midnight Moon   1
     Original Hummus   1
      Organic Garnet Sweet Potato (Yam)   1
       Guacamole   1
        Organic Large Green Asparagus   1
         Lemon Hummus   1
          Rice Cracker Snacks   1
           Almond Nut 

...

    Moist Supreme Classic Yellow Cake Mix   1
     Creamy Classic Vanilla Frosting   1
      Creamy Chocolate Frosting   1
       Birthday Candle   1
    Raisin   1
   Alfredo Pasta Sauce   2
    Chicken Taquitos   1
     Organic Coconut Yogurt   1
      Organic Whole Milk Washington Black Cherry Yogurt   1
       Three Cheese Mini Pizza Bagels Frozen Snacks   1
        Salty Peanut Pretzel Granola Bars   1
         Organic  Sweet   1
          SALSA        FRNTR CHPTL SALSA   1
           Super Green Juice Blend Smoothie   1
            Protein Power Greens Smoothie   1
   Freshly Grated Cheese   2
    Cauliflower Head   1
   Mustard   1
   Handle-Tie   1
   Original Blend   1
   Pure Foods Sea Salt Iodized   1
   Sriracha Chili Sauce   1
    Raspberry   1
     Genuine Chocolate Flavor Syrup   1
      Paper Towel   1
       Walnut Dressing   1
        Catalina Fat Free Dressing   1
   Organic Vegetable Broth   1
    Sliced White Mushrooms   1
     Icelandic Style Fat Free Plain Yogurt

      Whipped Original Cream Cheese Spread   1
       Grilling Spray   1
   Party Size   5
    Brown Rice Cakes   1
     Blueberry Beet   1
      Real Cheddar Baked Cheese Puffs   1
    Organic Spring Jasmine Green Tea   1
    Wild Blueberry Preserves   1
     Regular Concentrated Bleach   1
    Thin Spaghetti No 11   1
   Original Tempeh   1
   Whole Milk With Vitamin D   1
    BBQ Chicken Crispy Thin Crust Pizza   1
     Signature Pepperoni Crispy Thin Crust Pizza   1
   Organic Mandarins   2
    Organic Blueberries Clamshell   1
   Sundried Tomato   1
    Basil Wheat Thins   1
     Triscuit Roasted Garlic Baked Whole Grain Crackers   1
      Restaurant Style   1
   Organic Spinach Bunch   1
    Organic Purple Kale   1
     Coconut Milk INon Dairy Frozen Dessert Coconut   1
   smartwater® Electrolyte Enhanced Water   1
    Flexible Straws   1
   Russian Lowfat Yogurt   1
   Baking Powder   2
    Milk Chocolate Bar   1
     Hazelnuts in Milk Chocolate   1
    Uncured Bacon   1
     Po

   Total 2% Greek Strained Yogurt with Cherry 5.3 oz   1
    Country White Bread   1
     Golden Sweet Potato   1
      Sprouted Whole Wheat Bread   1
       Diet Root Beer   1
        Barbeque Potato   1
         Chocolate Peanut Butter Meal Bar   1
          Pepperoni Party Pizza   1
           Corn Chex Cereal   1
            Omeprazole Acid Reducer Tablets   1
             Charcoal Lighter Fluid   1
              Chocolate Chip Granola Meal Bars   1
               Charcoal Briquettes Mesquite   1
   Organic Greek Nonfat Yogurt With Mixed Berries   1
    Whole Hearts of Palm   1
     Organic Pitted Green Olives   1
      Wild Arugula   1
       Goat's Milk Cheese   1
   French Baguettes   1
   Organic Animal Crackers   2
    Multi Grain Cheerios   1
    All-Purpose Flour   1
     Granulated Sugar   1
   Wakame   1
   Silver Grade   1
   Vegetable Base   1
    Ready-to-Use   1
   Organic Classic Hummus   1
   Minis   1
   Organic Vanilla Almond Milk   2
    Ginger Root Beer   1
    P

   Magic Eraser Extra Power   1
    Mega Shower Foamer with Ultra Cling   1
     Ultra Downy® Mountain Spring™ Liquid Fabric Conditioner 51 Fl oz. 60 loads Fabric Enhancers   1
   Concentrated Bleach   1
    Glade Rainshower Fragrance   1
   Organic Orzo   1
    Green Curry Paste   1
     Sriracha Popcorn   1
   Uncured Black Forest Ham   1
    Hot   1
     Ice Cream   1
   Family Pack   3
    Orange Smooth Fiber Supplement   1
    French Roast   1
    Tender white meat chicken in a red chile lime sauce with a medley of roasted corn   1
     Toasted Oats Cereal   1
   Chives   1
   Stringless Sugar Snap Peas   2
    Organic Light in Sodium Lentil Vegetable Soup   1
     Vitamin Water Zero Rise Orange   1
      VitaminWater Zero™ XXX Acai Blueberry Pomegranate   1
       Zero Go-Go Mixed Berry Vitamin Water   1
        Organic Chunky Vegetable Soup   1
         Revive Zero Vitamin Water   1
          Organic Low Fat Black Bean Vegetable Soup   1
           Traditional Hearty Chicken and

      Organic Diced Fire Roasted Tomatoes   1
       Cannellini White Kidney Beans No Salt Added   1
        Organic Ground Cumin   1
         Humboldt Fog   1
          Fresh Mozzarella   1
           Great Northern Beans   1
            Almond Paleo Bread Non GMO Gluten Free   1
   Honey Wheat Enriched Bread   1
    Simply Strawberry Gelato   1
   Limeade   1
    Sweet Iced Tea   1
     Berry Punch Flavored Fruit Drink   1
      WetJet Wood Floor Cleaner Refill Blossom Breeze   1
       7 Up Lemon Lime Soda   1
        Rice Drink   1
         Horchata Original Milk   1
   Chocolate Milk   1
    World Cuisine Certified Halal Chicken Tikka Masala With Basmati Rice   1
     vitaminwater® XXX Acai Blueberry Pomegranate   1
      Blueberry Scones   1
   Unsalted Butter Quarters   1
    Panko Breaded Chicken Breast Tenderloins   1
   Original English Muffins   1
    Unscented Liquid Laundry Detergent   1
     Milano Dark Chocolate Cookies   1
   Children's Bubble Gum Fever Reducer and Pain

In [18]:
findPrefixPath('Bag of Organic Bananas', myHeaderTab['Bag of Organic Bananas'][1])

{frozenset({'Banana'}): 8}

In [19]:
#FpGrowth(dataset, min_support)
FpGrowth(simpDat, 0.001)

support                                           itemsets
0     0.083187                           (Bag of Organic Bananas)
1     0.043816                             (Organic Hass Avocado)
2     0.019529                                   (Cucumber Kirby)
3     0.014397                      (Organic Whole String Cheese)
4     0.005070                            (Organic Celery Hearts)
...        ...                                                ...
2417  0.001252  (Icelandic Style Skyr Blueberry Non-fat Yogurt...
2418  0.001127            (Chicken, Apple Smoked Chicken Sausage)
2419  0.001127  (Thin Crust Margherita Pizza with Fresh Mozzar...
2420  0.001127  (Amaranth Waffles, Organic Gluten Free Chia Pl...
2421  0.001127                 (Rosemary, Olive Oil Quinoa Blend)

[2422 rows x 2 columns]